# CS/INFO 5304 Assignment 2: Recommender Systems
Credit: 35 points + possible bonus (10 points)

Due date: April 19th, 11:00PM
 
The goal of the assignment is to get familiar with different types of recommender systems. Specifically, we are going to build a system that can recommend Yelp businesses to users.

In [1]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt

In [2]:
pd.set_option('display.max_columns', None)

In [3]:
users = pd.read_csv("user-business.csv", header=None) # The columns are separated by a space.
users.head() # Rij = 1 if the user has visited&rated that business. Otherwise  Rij = 0.

0    1    2    3    4    5    6    7    8    9    10   11   12   13   14   \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
3    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   15   16   17   18   19   20   21   22   23   24   25   26   27   28   29   \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    1   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    1   
3    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    1   

   30   31   32   33   34   35   36   37   38   39   40   41   42   43   44   \
0    0    0    0    1    1    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    1    1    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    1    1    0    0    0    0    0    0    0    0    0    0   
3    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    1    1    0    0    0    0    0    0    0    0    0    0   

   45   46   47   48   49   50   51   52   53   54   55   56   57   58   59   \
0    0    0    0    1    0    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
3    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   60   61   62   63   64   65   66   67   68   69   70   71   72   73   74   \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
3    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   75   76   77   78   79   80   81   82   83   84   85   86   87   88   89   \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
3    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   90   91   92   93   94   95   96   97   98   99   100  101  102  103  104  \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
3    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   105  106  107  108  109  110  111  112  113  114  115  116  117  118  119  \
0    0    1    0    0    0    0    0    1    0    0    0    0    0    0    0   
1    0    1    0    0    0    0    0    1    0    0    0    0    0    0    0   
2    0    1    0    0    0    0    0    1    0    0    0    0    0    0    0   
3    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    1    0    0    0    0    0    0    0    0    0    0    0    0    0   

   120  121  122  123  124  125  126  127  128  129  130  131  132  133  134  \
0    0    0    0    0    1    0    0    0    0    0    0    0    0    0    

In [4]:
users.info() # ratings matrix R, where each row corresponds to a user and each column corresponds to a business

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14397 entries, 0 to 14396
Columns: 1000 entries, 0 to 999
dtypes: int64(1000)
memory usage: 109.8 MB


In [5]:
users.shape # 14397 active users and 1000 popular businesses on Yelp (column name = index #)

(14397, 1000)

In [6]:
users.describe()

0             1             2             3             4    \
count  14397.000000  14397.000000  14397.000000  14397.000000  14397.000000   
mean       0.006668      0.008474      0.004168      0.004584      0.013475   
std        0.081388      0.091667      0.064424      0.067554      0.115301   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max        1.000000      1.000000      1.000000      1.000000      1.000000   

                5             6             7             8             9    \
count  14397.000000  14397.000000  14397.000000  14397.000000  14397.000000   
mean       0.002501      0.002709      0.015906      0.012850      0.001042   
std        0.049944      0.051978      0.125117      0.112631      0.032263   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max        1.000000      1.000000      1.000000      1.000000      1.000000   

                10            11            12            13            14   \
count  14397.000000  14397.000000  14397.000000  14397.000000  14397.000000   
mean       0.000764      0.004376      0.000764      0.004793      0.000278   
std        0.027632      0.066008      0.027632      0.069065      0.016667   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max        1.000000      1.000000      1.000000      1.000000      1.000000   

                15            16            17            18            19   \
count  14397.000000  14397.000000  14397.000000  14397.000000  14397.000000   
mean       0.001806      0.012642      0.004029      0.006599      0.006599   
std        0.042459      0.111725      0.063346      0.080966      0.080966   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max        1.000000      1.000000      1.000000      1.000000      1.000000   

                20            21            22            23            24   \
count  14397.000000  14397.000000  14397.000000  14397.000000  14397.000000   
mean       0.002014      0.000972      0.003681      0.001806      0.001667   
std        0.044837      0.031170      0.060564      0.042459      0.040796   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max        1.000000      1.000000      1.000000      1.000000      1.000000   

                25            26            27            28            29   \
count  14397.000000  14397.000000  14397.000000  14397.000000  14397.000000   
mean       0.002431      0.004168      0.003265      0.003890      0.006668   
std        0.049248      0.064424      0.057045      0.062248      0.081388   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000

In [7]:
busi = pd.read_csv("business.csv", header=None)
busi.head() # businesses, in the same order as the columns of matrix R (user df)

0
0              Pittock Mansion
1              Legal Sea Foods
2  Eurasia Sushi Bar & Seafood
3                Piece of Cake
4                Sapporo Ramen

In [8]:
busi.shape # row number corresponds to index in user matrix

(1000, 1)

In [9]:
busi.columns = ['Business']

In [10]:
busi.head()

Business
0              Pittock Mansion
1              Legal Sea Foods
2  Eurasia Sushi Bar & Seafood
3                Piece of Cake
4                Sapporo Ramen

## Part A: user – user recommender system [10 points]
In this assignment we are going to implement three types of recommender systems. We are then going to compare the results of these systems for the 4th user (index starting from 1) of the dataset. Let’s call him Alex (row index 3). Based on Alex’s behavior on the other businesses, you need to give Alex recommendations on the first 100 businesses. We will then see if our recommendations match what Alex had in fact visited.

Let S denote the set of the first 100 businesses (the first 100 columns of the matrix). From all the businesses in S, which are the five that have the highest similarity scores (rAlex,b) for Alex? What are their similarity scores? In case of ties between two businesses, choose the one with a smaller index. Do not write the index of the businesses, write their names using the file business.csv.


In [11]:
S = users.iloc[:,:100]
S.head()

0   1   2   3   4   5   6   7   8   9   10  11  12  13  14  15  16  17  18  \
0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
1   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
2   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
3   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
4   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   

   19  20  21  22  23  24  25  26  27  28  29  30  31  32  33  34  35  36  37  \
0   0   0   0   0   0   0   0   0   0   0   1   0   0   0   1   1   0   0   0   
1   0   0   0   0   0   0   0   0   0   0   0   0   0   0   1   1   0   0   0   
2   0   0   0   0   0   0   0   0   0   0   1   0   0   0   1   1   0   0   0   
3   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
4   0   0   0   0   0   0   0   0   0   0   1   0   0   0   1   1   0   0   0   

   38  39  40  41  42  43  44  45  46  47  48  49  50  51  52  53  54  55  56  \
0   0   0   0   0   0   0   0   0   0   0   1   0   0   0   0   0   0   0   0   
1   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
2   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
3   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
4   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   

   57  58  59  60  61  62  63  64  65  66  67  68  69  70  71  72  73  74  75  \
0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
1   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
2   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
3   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
4   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   

   76  77  78  79  80  81  82  83  84  85  86  87  88  89  90  91  92  93  94  \
0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
1   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
2   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
3   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   
4   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   

   95  96  97  98  99  
0   0   0   0   0   0  
1   0   0   0   0   0  
2   0   0   0   0   0  
3   0   0   0   0   0  
4   0   0   0   0   0

In [12]:
S.shape

(14397, 100)

In [13]:
# we have erased the first 100 entries of Alex’s row in the matrix, and replaced them by 0s
S.iloc[3].value_counts()

0    100
Name: 3, dtype: int64

In [14]:
R = users.iloc[:,100:]
R.head()

100  101  102  103  104  105  106  107  108  109  110  111  112  113  114  \
0    0    0    0    0    0    0    1    0    0    0    0    0    1    0    0   
1    0    0    0    0    0    0    1    0    0    0    0    0    1    0    0   
2    0    0    0    0    0    0    1    0    0    0    0    0    1    0    0   
3    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    1    0    0    0    0    0    0    0    0   

   115  116  117  118  119  120  121  122  123  124  125  126  127  128  129  \
0    0    0    0    0    0    0    0    0    0    1    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    1    0    0    0    0    0   
3    0    0    0    0    0    0    0    0    1    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    1    0    0    0    0    0   

   130  131  132  133  134  135  136  137  138  139  140  141  142  143  144  \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
3    0    0    0    0    1    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   145  146  147  148  149  150  151  152  153  154  155  156  157  158  159  \
0    0    0    0    0    0    0    0    0    0    0    0    1    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
3    0    0    0    0    0    0    0    0    0    0    0    0    0    1    0   
4    0    0    0    0    1    0    0    0    0    0    0    1    0    0    0   

   160  161  162  163  164  165  166  167  168  169  170  171  172  173  174  \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
3    0    0    0    0    0    0    0    0    0    1    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   175  176  177  178  179  180  181  182  183  184  185  186  187  188  189  \
0    0    0    0    0    0    0    0    1    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    1    0    1    0    0    0    0    0   
3    0    0    0    0    0    1    1    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   190  191  192  193  194  195  196  197  198  199  200  201  202  203  204  \
0    0    0    0    0    0    0    0    1    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    1   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
3    0    0    0    0    0    0    0    0    1    0    1    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    1   

   205  206  207  208  209  210  211  212  213  214  215  216  217  218  219  \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
3    0    0    0    0    0    1    0    0    1    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   220  221  222  223  224  225  226  227  228  229  230  231  232  233  234  \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    

In [15]:
# Alex
ALEX = R.iloc[3].copy()

In [16]:
ALEX

100    0
101    0
102    0
103    0
104    0
      ..
995    0
996    0
997    0
998    0
999    0
Name: 3, Length: 900, dtype: int64

In [17]:
ALEX.value_counts()

0    829
1     71
Name: 3, dtype: int64

In [18]:
R = R.drop(3)

In [19]:
R.shape

(14396, 900)

In [20]:
R.head()

100  101  102  103  104  105  106  107  108  109  110  111  112  113  114  \
0    0    0    0    0    0    0    1    0    0    0    0    0    1    0    0   
1    0    0    0    0    0    0    1    0    0    0    0    0    1    0    0   
2    0    0    0    0    0    0    1    0    0    0    0    0    1    0    0   
4    0    0    0    0    0    0    1    0    0    0    0    0    0    0    0   
5    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   115  116  117  118  119  120  121  122  123  124  125  126  127  128  129  \
0    0    0    0    0    0    0    0    0    0    1    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    1    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    1    0    0    0    0    0   
5    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   130  131  132  133  134  135  136  137  138  139  140  141  142  143  144  \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
5    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   145  146  147  148  149  150  151  152  153  154  155  156  157  158  159  \
0    0    0    0    0    0    0    0    0    0    0    0    1    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    1    0    0    0    0    0    0    1    0    0    0   
5    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   160  161  162  163  164  165  166  167  168  169  170  171  172  173  174  \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
5    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   175  176  177  178  179  180  181  182  183  184  185  186  187  188  189  \
0    0    0    0    0    0    0    0    1    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    1    0    1    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
5    0    0    0    0    0    0    0    1    0    0    0    0    0    0    0   

   190  191  192  193  194  195  196  197  198  199  200  201  202  203  204  \
0    0    0    0    0    0    0    0    1    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    1   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    1   
5    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   205  206  207  208  209  210  211  212  213  214  215  216  217  218  219  \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
1    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
2    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
4    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   
5    0    0    0    0    0    0    0    0    0    0    0    0    0    0    0   

   220  221  222  223  224  225  226  227  228  229  230  231  232  233  234  \
0    0    0    0    0    0    0    0    0    0    0    0    0    0    0    

In [21]:
from numpy import dot
from numpy.linalg import norm

In [22]:
def cos_sim(a,b):
    return dot(a, b)/(norm(a)*norm(b))

In [23]:
# find similarity between users (cosine similarity of other users with Alex excluding the first 100 businesses)
cosims = []
for user in R.index.values:
    cosims += [cos_sim(ALEX, R.loc[user])]

In [24]:
# NOTE TO SELF
# .loc --> index name (R.loc[14396] works)
# .iloc --> index (R.iloc[14396] IndexError: single positional indexer is out-of-bounds)

In [25]:
cosims

[0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.03955938860646178,
 0.0,
 0.0,
 0.4681221630826506,
 0.0723930024686082,
 0.0,
 0.0,
 0.0,
 0.4830679802010464,
 0.0,
 0.0,
 0.020353137525332635,
 0.0,
 0.0,
 0.0,
 0.06293860187225167,
 0.5004292214714362,
 0.0,
 0.0,
 0.0,
 0.021667569500871973,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.02797271194322297,
 0.4485613040162566,
 0.0,
 0.0,
 0.0,
 0.0,
 0.02283962366091772,
 0.021667569500871973,
 0.0,
 0.0,
 0.0,
 0.0,
 0.48776425689910546,
 0.5158454996186951,
 0.0,
 0.27407548393101266,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.023735633163877064,
 0.0,
 0.0,
 0.24241780349669298,
 0.0,
 0.019510570275964218,
 0.03171807398477756,
 0.3454041975020422,
 0.020979533957417223,
 0.0,
 0.3633761873336319,
 0.03064257065179478,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.39559388606461776,
 0.0,
 0.019510570275964218,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.38846548443275297,
 0.028783683125170184,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0484501

In [26]:
len(cosims)

14396

In [27]:
# ratings matrix R without Alex
compare = users.drop(3)
compare.shape

(14396, 1000)

In [28]:
# take transpose of original ratings matrix (with first 100)
# and multiply (not dot) it with the similarities 
ratings = compare.T * cosims
ratings.shape

(1000, 14396)

In [30]:
ratings.head()

0      1      2      4      5      6      7      8      9         10     \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0  0.000000   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0  0.000000   
2    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0  0.000000   
3    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0  0.468122   
4    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0  0.000000   

      11     12     13     14     15     16     17        18     19     20     \
0  0.000000    0.0    0.0    0.0    0.0    0.0    0.0  0.020353    0.0    0.0   
1  0.072393    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0   
2  0.000000    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0   
3  0.000000    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0   
4  0.000000    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0   

   21     22     23     24     25     26        27     28     29     30     \
0    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0    0.0   
2    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0    0.0   
3    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0    0.0   
4    0.0    0.0    0.0    0.0    0.0    0.0  0.021668    0.0    0.0    0.0   

   31     32     33     34     35     36     37     38     39     40     \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

   41     42     43     44     45     46        47     48     49     50     \
0    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0    0.0   
2    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0    0.0   
3    0.0    0.0    0.0    0.0    0.0    0.0  0.515845    0.0    0.0    0.0   
4    0.0    0.0    0.0    0.0    0.0    0.0  0.000000    0.0    0.0    0.0   

   51     52     53     54     55     56     57     58     59     60     \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

   61     62     63     64     65     66     67     68     69     70     \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

   71     72     73     74     75     76     77     78     79     80     \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

   81     82     83     84     85     86     87     88     89     90     \
0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3    

In [31]:
# sum over rows to get vector of predictions for Alex's ratings (only care about first 100 rows)
preds = ratings.sum(axis=1)

In [32]:
preds.shape

(1000,)

In [33]:
preds.max()

89.8106386251313

In [34]:
unknown = preds[:100]
unknown.max()

43.039526922656655

In [35]:
unknown.sort_values(ascending=False)[:10] # inplace=False by default

7     43.039527
61    33.598188
16    33.263225
39    32.782940
3     12.626244
70    11.332088
57     8.280394
67     7.828182
98     7.801835
71     6.242388
dtype: float64

In [36]:
uu_top5 = unknown.sort_values(ascending=False)[:5].index
uu_top5

Int64Index([7, 61, 16, 39, 3], dtype='int64')

In [37]:
busi.loc[uu_top5]

Business
7   Papi's Cuban & Caribbean Grill
61                     Seven Lamps
16                       Loca Luna
39                     Farm Burger
3                    Piece of Cake

From all the businesses in S, the five that have the highest similarity scores for Alex in order from highest to lowest score are Papi's Cuban & Caribbean Grill, Seven Lamps, Loca Luna, Farm Burger, and Piece of Cake.

In [38]:
print("Their similarity scores are: ", unknown[uu_top5].values)

Their similarity scores are:  [43.03952692 33.59818778 33.26322496 32.78294006 12.6262441 ]


## Part B: item – item recommender system [10 points]
From all the businesses in S (first 100 businesses), which are the five that have the highest similarity scores for Alex?  In case of ties between two businesses, choose the one with a smaller index. Again, hand in the names of the businesses and their similarity score.

In [39]:
# find items (businesses) with similar ratings
compare.shape # exclude the entries of Alex

(14396, 1000)

In [40]:
# Alex's ratings from the original matrix (1000)
origALEX = users.iloc[3].copy()

In [41]:
origALEX.value_counts()

0    929
1     71
Name: 3, dtype: int64

In [42]:
origALEX.shape

(1000,)

In [43]:
from sklearn.metrics.pairwise import cosine_similarity

In [44]:
matrix = pd.DataFrame(cosine_similarity(users.T))

In [45]:
matrix.shape

(1000, 1000)

In [46]:
# take dot product of the similarities (1000,1000) with Alex's ratings from the original matrix (1000)
# to get predictions for Alex's ratings of the businesses
item_preds = dot(matrix, origALEX)

In [47]:
item_preds.shape

(1000,)

In [48]:
item_preds

array([7.24723362e-02, 4.43704079e-01, 9.14430147e-02, 3.70828839e+00,
       1.06904680e-01, 2.51245760e-02, 2.12791488e-01, 6.77409878e+00,
       1.56654367e-01, 0.00000000e+00, 6.68598661e-02, 3.23224758e-02,
       2.15162280e-01, 1.23701769e-01, 5.85728100e-01, 2.99134982e-02,
       5.82100444e+00, 0.00000000e+00, 7.26110913e-02, 3.95779742e-03,
       0.00000000e+00, 5.46423743e-02, 1.82781521e-02, 0.00000000e+00,
       5.73434281e-02, 2.47611940e-02, 8.95143593e-03, 2.17442691e-02,
       1.32175776e-01, 1.73046394e-01, 4.85050554e-02, 5.20156487e-03,
       1.81848242e-02, 0.00000000e+00, 0.00000000e+00, 5.13503371e-02,
       2.50201429e+00, 2.16290263e-01, 4.49844438e-02, 6.52285649e+00,
       2.31078370e-01, 1.14435453e-01, 4.11114125e-02, 7.61080395e-02,
       2.15960309e+00, 2.25748014e-02, 3.15467130e-01, 1.19772369e-01,
       0.00000000e+00, 4.55093953e-02, 7.45087215e-02, 1.89320611e-02,
       2.66645546e-01, 6.55147725e-02, 1.58703422e-01, 1.10435263e-01,
      

In [49]:
ipreds = pd.Series(item_preds)

In [50]:
ipreds.max()

8.689412523655799

In [51]:
# select first 100
ipreds = ipreds[:100]
ipreds

0     0.072472
1     0.443704
2     0.091443
3     3.708288
4     0.106905
        ...   
95    0.000000
96    0.100655
97    0.028760
98    2.395271
99    0.183303
Length: 100, dtype: float64

In [52]:
ipreds.max()

6.774098776171186

In [53]:
# sort and look at top (check for ties) 
ipreds.sort_values(ascending=False)[:10]

7     6.774099
39    6.522856
61    6.404469
16    5.821004
3     3.708288
70    3.446701
67    3.379060
71    2.853051
57    2.834543
36    2.502014
dtype: float64

In [54]:
# select the top 5 and get their indices corresponding to which businesses
ii_top5 = ipreds.sort_values(ascending=False)[:5].index
ii_top5

Int64Index([7, 39, 61, 16, 3], dtype='int64')

In [55]:
busi.loc[ii_top5] # top 5 recommended businesses for Alex in S

Business
7   Papi's Cuban & Caribbean Grill
39                     Farm Burger
61                     Seven Lamps
16                       Loca Luna
3                    Piece of Cake

In [56]:
print("Their similarity scores are: ", ipreds[ii_top5].values)

Their similarity scores are:  [6.77409878 6.52285649 6.40446897 5.82100444 3.70828839]


## Part C: Latent hidden model recommender system [15 points]
Latent model recommender system is the most popular type of recommender system in the market today. Here we perform a matrix factorization of the ratings matrix R into two matrices U and V where U is considered as the user features matrix and V is the movie features matrix. Note that the features are ‘hidden’ and need not be understandable to users. Hence the name latent hidden model. (refer slides for more information)

The latent model can be implemented by performing a singular value decomposition (SVD) that factors the matrix into three matrices
 
R = U Σ VT
 
where R is user ratings matrix, U is the user “features” matrix, Σ is the diagonal matrix of singular values (essentially weights), and VT is the movie “features” matrix. U and VT are orthogonal, and represent different things. U represents how much users “like” each feature and VT represents how relevant each feature is to each business.
To get the lower rank approximation, we take these matrices and keep only the top k features (k factors), which we think of as the k most important underlying taste and preference vectors.
 
With k set to 10, perform SVD to identify the U and V matrices. You can then multiply the matrices to estimate the following
 
R* = U Σ VT

From the R* matrix, select the top 5 businesses for Alex in S (first 100 businesses). In case of ties between two businesses, choose the one with a smaller index. Again, hand in the names of the businesses and their similarity score.
 
Hint: You can use SVD in surprise package, or numpy, scipy

In [57]:
from numpy.linalg import svd

In [58]:
u,s,vh = svd(users) # user factors matrix, singular values/weights, movie factors matrix

In [59]:
u.shape

(14397, 14397)

In [60]:
s.shape

(1000,)

In [61]:
s[:10] # descending order

array([43.23323189, 39.71119985, 34.85853609, 31.07054649, 28.49541399,
       28.4518733 , 23.93105429, 22.45492933, 22.25092047, 21.26226817])

In [62]:
diag = np.diag(s)
diag.shape

(1000, 1000)

In [63]:
vh.shape

(1000, 1000)

In [64]:
# keep only the top k=10 features (10 factors)
ku = u[:, :10]
ks = diag[:10, :10]
kvh = vh[:10,:]
ku.shape, ks.shape, kvh.shape

((14397, 10), (10, 10), (10, 1000))

In [65]:
recon = ku @ ks @ kvh

In [66]:
# reconstructed ratings matrix should be (14397,1000) with Alex's 100 missing entries filled in
recon.shape

(14397, 1000)

In [67]:
recon[3][:100]

array([-4.56322892e-03,  1.71963669e-02,  2.24149075e-03,  2.99354394e-01,
       -4.92129941e-03, -1.95313499e-03,  1.39142235e-02,  1.19050642e+00,
       -1.71748104e-02, -1.37636135e-03,  1.64473969e-03, -2.41582558e-03,
        2.24237845e-03,  1.55578875e-03,  7.95076905e-03, -3.25625597e-03,
        8.76254571e-01, -3.14293964e-03, -1.05953381e-03, -3.40317297e-03,
       -7.99315795e-04,  2.35883671e-04, -1.35226419e-03, -1.19413534e-03,
        7.16194696e-05, -2.78296748e-03, -2.27767997e-04, -5.19911643e-04,
        3.66447324e-03,  5.98461993e-03, -6.66320851e-03, -4.05248341e-03,
       -1.36478808e-03, -4.98618639e-03, -5.74884029e-03, -4.79565470e-03,
        1.20566297e-01,  1.25875857e-02, -3.38659435e-03,  8.57826388e-01,
        1.16731682e-04, -4.50766929e-03, -1.12119022e-02,  1.31182072e-03,
        1.23774789e-01, -2.00480200e-03,  1.02997184e-02,  3.30231710e-03,
       -6.75711882e-03, -5.46017589e-03, -8.49903340e-03, -1.12896392e-03,
        3.71224035e-03, -

In [68]:
recon[3][:100].max()

1.1905064199911002

In [69]:
rec = pd.Series(recon[3][:100])

In [70]:
rec.max()

1.1905064199911002

In [71]:
# sort and look at top (check for ties) 
rec.sort_values(ascending=False)[:10]

7     1.190506
16    0.876255
39    0.857826
61    0.817947
3     0.299354
70    0.213350
67    0.194277
98    0.171549
57    0.165042
71    0.139503
dtype: float64

In [72]:
# select the top 5 and get their indices corresponding to which businesses
svd_top5 = rec.sort_values(ascending=False)[:5].index
svd_top5

Int64Index([7, 16, 39, 61, 3], dtype='int64')

In [73]:
busi.loc[svd_top5] # names of the businesses

Business
7   Papi's Cuban & Caribbean Grill
16                       Loca Luna
39                     Farm Burger
61                     Seven Lamps
3                    Piece of Cake

In [74]:
# similarity scores
print("Their similarity scores are: ", rec[svd_top5].values)

Their similarity scores are:  [1.19050642 0.87625457 0.85782639 0.81794731 0.29935439]
